<a href="https://colab.research.google.com/github/tranhuuan170302/Recommended-system-of-information-technology-jobs-at-Viet-Nam/blob/main/Model_BERTopic.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Mô tả cách thức xử lí<br>
### Bước 1: thực hiện đọc 1 file csv và lấy 2 cột chính là cột "Summary", "JobUrl".<br>
  + cột Summary: là cột mô tả công việc và yêu cầu, kinh nghiệm trong công việc.<br>
  + cột JobUrl: là cột tên công viêc.<br>


### Bước 2: Thực hiện tiền xử lí dữ liệu.<br>
  + xóa kí tự '\n'. <br>
  + Tạo một danh sách keyword (danh sách keyword này dựa theo thuật toán tf-idf để lựa chọn ra các danh sách các keyword mà em được cho là nó quan trọng nhất).<br>
  + Sau đó đơn giản hóa các keyword này đi ví dụ: programmer => program để có thể dễ lấy được dữ liệu một cách tổng quan nhất.<br>
  + Giá trị của cột Summary là một đoạn text. Vì vậy ta chia nhỏ ra thành các câu để dễ thực hiện việc xử lí dữ liệu theo keyword đông thời giúp mô hình BERTopic tốt hơn.<br>
  + Lọc dữ liệu từ các câu theo các keywords đã khởi tạo. Các câu có từ nằm trong keywords sẽ được giữ lại, các câu không có thì sẽ có giá trị None.<br>
  + các dòng mang giá trị None sẽ được xóa hết đi. Các câu có giá trị khác None sẽ được thực hiện xóa bỏ các từ stopword ví dụ: is, a, the, and,...<br>

    

### Bước 3: áp dụng mô hình BERTopic. Đây là mô hình thuật toán phân cụm. Thuật toán BERTopic trải qua 3 giao đoạn. <br>
  + Giai đoạn 1: Đọc tài liệu. Đầu vào sẽ là cột 'review_lemmatized' cột này đã được đi qua xử lí ở bước 2. BERTopic sẽ chuyển các câu này thày một vector.<br>
  + Bước 2: phân cụm tài liệu.<br>
    + Sau khi thực hiện giai đoạn 1 thì sẽ thực hiện mô hình phân cụm các câu dựa trên các vector này. Mô hình sẽ sử dụng UMAP (Uniform Manifold Approximation & Projection) là một thuật toán để giảm chiều dữ liệu (Mỗi topic đều được thể hiện thông qua một tập hợp các từ lại với nhau. Nhưng có một vài từ thì lại không có mang tính chất thể hiện nhiều. Vì vậy ta sử dụng thuật toán UMAP để giảm thiểu nó đi).<br>
  + Bước 3: Topic Representation.<br>
    + Sau khi mỗi câu đã được phân cụm rồi. Thì thuật toán sẽ áp một c-tf-idf dựa trên tf-idf để chọn ra nhưng từ quan trọng nhất trong câu để đại diện.<br>


### Bước 4: Thực hiện kiểm tra mô hình thông qua trực quan hóa dữ liệu. <br>

# Import libaries

In [86]:
# Install bertopic
!pip install bertopic

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [87]:
# Data processing
import pandas as pd
import numpy as np

# Text preprocessiong
import nltk
nltk.download('stopwords')
nltk.download('omw-1.4')
nltk.download('wordnet')
wn = nltk.WordNetLemmatizer()

# Topic model
from bertopic import BERTopic

# Dimension reduction
from umap import UMAP

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /root/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [88]:
text = pd.read_csv('/content/drive/MyDrive/indeed/resultData.csv')

In [89]:
text.head()

Unnamed: 0                              JobTitle            Company  \
0           0                        .Net Developer           SmartDev   
1           1            Intern / Fresher Developer     DXC Technology   
2           2  .NET Developer (Middle/Senior level)              SIOUX   
3           3         Jun/Mid/Senior .NET Developer  Saigon Technology   
4           4     Web Developer (.NET, ASP.NET, C#)           NPV Corp   

                Location                      PostDate ExtractDate  \
0                Ðà Nẵng    Posted\nPosted 14 days ago  2023-01-25   
1  Thành phố Hồ Chí Minh  Employer\nActive 22 days ago  2023-01-25   
2                Ðà Nẵng   Posted\nPosted 30+ days ago  2023-01-25   
3                Ðà Nẵng    Posted\nPosted 18 days ago  2023-01-25   
4                Ðà Nẵng    Posted\nPosted 16 days ago  2023-01-25   

                                             Summary            JobUrl  
0  Company Description\nSmartDev is a leading pro...  .NET Developer\n  
1  Overview:\nHow would you like to join an inter...  .NET Developer\n  
2  Sioux Group was founded in 1996 in the Netherl...  .NET Developer\n  
3  Up to $2,200\nJunior, Middle, Senior\nDa Nang\...  .NET Developer\n  
4  Web Developer (.NET, ASP.NET, C#)\nNPV Corp\nỨ...  .NET Developer\n

In [90]:
review = text[['Summary', 'JobUrl']]

In [91]:
review.shape

(4379, 2)

In [92]:
review['Summary'] = review['Summary'].str.replace('\n', '')
review['JobUrl'] = review['JobUrl'].str.replace('\n', '')

In [93]:
# Remove stopwords
stopwords = nltk.corpus.stopwords.words('english')

In [94]:
review = review.reset_index()

In [95]:
review.head()

index                                            Summary          JobUrl
0      0  Company DescriptionSmartDev is a leading provi...  .NET Developer
1      1  Overview:How would you like to join an interna...  .NET Developer
2      2  Sioux Group was founded in 1996 in the Netherl...  .NET Developer
3      3  Up to $2,200Junior, Middle, SeniorDa NangFull-...  .NET Developer
4      4  Web Developer (.NET, ASP.NET, C#)NPV CorpỨng T...  .NET Developer

In [96]:
text['Summary'][0]

'Company Description\nSmartDev is a leading provider of global software solutions. The company was established in 2014 and is a wholly owned subsidiary of Verysell Technologies Group (Switzerland).\nSmartDev combines renowned Swiss quality with the Vietnamese passion to provide excellence and value. We brings together smart people both internally and externally to create partnerships that push boundaries and challenge the status quo.\nAs part of SmartDev’s aggressive growth plan we are looking to expand our development team, we (https://smartdev.com/) offers tailor-made mobile apps and websites with the most popular frontend and back-end technologies. We are currently works with about 140 developers.\n\nJob Description\n\nYou will report to PM (Project Manager)\nCollaborate with teams to product software design and architecture\nWrite clean, scalable code using .Net programming languages\nTest and deploy application and systems\nRevise, update, refactor and debugs code\nDevelop documen

In [97]:
import re
from nltk.stem import PorterStemmer
from nltk import pos_tag

In [98]:
# got these keywords by looking at some examples and using existing knowledge.
tool_keywords1 = ['sql', 'linqpad', 'teamcity', 'octopus', 'ncrunch', 'nuget', 'nunit', 'omnisharp', 'jetBrains rider', 'windbg', '.net reflector',
                  'reSharper', 'python', 'pytorch', 'sql', 'mxnet', 'mlflow', 'einstein', 'theano', 'pyspark', 'solr', 'mahout', 'html', 'css',
                  'cassandra', 'aws', 'powerpoint', 'spark', 'pig', 'sas', 'java', 'nosql', 'docker', 'salesforce', 'scala', 'r',
                  'c', 'c++', 'net', 'tableau', 'pandas', 'scikitlearn', 'sklearn', 'matlab', 'scala', 'keras', 'tensorflow', 'clojure',
                  'caffe', 'scipy', 'numpy', 'matplotlib', 'vba', 'spss', 'linux', 'azure', 'cloud', 'gcp', 'mongodb', 'mysql', 'oracle', 
                  'redshift', 'snowflake', 'kafka', 'javascript', 'qlik', 'jupyter', 'perl', 'bigquery', 'unix', 'react',
                  'scikit', 'powerbi', 's3', 'ec2', 'lambda', 'ssrs', 'kubernetes', 'hana', 'spacy', 'tf', 'django', 'sagemaker',
                  'seaborn', 'mllib', 'github', 'git', 'elasticsearch', 'splunk', 'airflow', 'looker', 'rapidminer', 'birt', 'pentaho', 
                  'jquery', 'nodejs', 'd3', 'plotly', 'bokeh', 'xgboost', 'rstudio', 'shiny', 'dash', 'h20', 'h2o', 'hadoop', 'mapreduce', 
                  'hive', 'cognos', 'angular', 'nltk', 'flask', 'node', 'firebase', 'bigtable', 'rust', 'php', 'cntk', 'lightgbm', 
                  'kubeflow', 'rpython', 'unixlinux', 'postgressql', 'postgresql', 'postgres', 'hbase', 'dask', 'ruby', 'julia', 'tensor',
                  # added r packages doesn't seem to impact the result
                  'dplyr','ggplot2','esquisse','bioconductor','shiny','lubridate','knitr','mlr','quanteda','dt','rcrawler','caret','rmarkdown',
                  'leaflet','janitor','ggvis','plotly','rcharts','rbokeh','broom','stringr','magrittr','slidify','rvest',
                  'rmysql','rsqlite','prophet','glmnet','text2vec','snowballc','quantmod','rstan','swirl','datasciencer', 'amazon web services', 'google cloud', 'sql server',
                  
                  
                  
                'statistics', 'cleansing', 'chatbot', 'cleaning', 'blockchain', 'causality', 'correlation', 'bandit', 'anomaly',
                'dashboard', 'geospatial', 'ocr', 'econometrics', 'pca', 'gis', 'svm', 'svd', 'tuning', 'hyperparameter', 'hypothesis',
                'salesforcecom', 'segmentation', 'biostatistics', 'unsupervised', 'supervised', 'exploratory',
                'recommender', 'recommendations', 'research', 'sequencing', 'probability', 'reinforcement', 'graph', 'bioinformatics',
                'chi', 'knn', 'outlier', 'etl', 'normalization', 'classification', 'optimizing', 'prediction', 'forecasting',
                'clustering', 'cluster', 'optimization', 'visualization', 'nlp', 'c#', 'negotiation', 'self learning', 
                'regression', 'logistic', 'nn', 'cnn', 'glm', 'sloving', 'ux ui', 'teamwork', 'creative thinking',
                'rnn', 'lstm', 'gbm', 'boosting', 'recurrent', 'convolutional', 'bayesian',
                'bayes', 'random forest', 'natural language processing', 'machine learning', 'decision tree', 'deep learning', 'experimental design',
                'time series', 'nearest neighbors', 'neural network', 'support vector machine', 'computer vision', 'machine vision', 'dimensionality reduction', 
                'text analytics', 'power bi', 'a/b testing', 'ab testing', 'chat bot', 'data mining',
                
                
                'bs', 'bachelor', 'undergraduate', 'certificate',
               'master', 'graduate', 'mba', 'intermediate',
               'phd', 'ph.d', 'ba', 'ma', 'it',
               'postdoctoral', 'postdoc', 'doctorate', 'new graduate', 'đại học']


In [99]:
ps = PorterStemmer()
tool_keywords1_set = set([ps.stem(tok) for tok in tool_keywords1])

In [100]:

df = pd.DataFrame(columns = ['index', 'review'])
for idx in review.index.unique():
  string = review['Summary'][idx]
  string = string.split('.')
  id = []
  txt = []
  
  for st in string:
    id.append(idx)
    txt.append(st)
    datax = pd.DataFrame(list(zip(id, txt)), columns = ['index', 'review'])
  df = pd.concat([df, datax])

In [101]:
df.head(15)

index                                             review
0      0  Company DescriptionSmartDev is a leading provi...
1      0   The company was established in 2014 and is a ...
2      0  SmartDev combines renowned Swiss quality with ...
3      0   We brings together smart people both internal...
4      0  As part of SmartDev’s aggressive growth plan w...
5      0  com/) offers tailor-made mobile apps and websi...
6      0   We are currently works with about 140 developers
7      0  Job DescriptionYou will report to PM (Project ...
8      0  Net programming languagesTest and deploy appli...
9      0                  Net DeveloperBe familiar with ASP
10     0  NET framework, SQL Server and design/ architec...
11     0                   Net languages (C#, Visual Basic 
12     0  Net), and HTML5/ CSS3Be familiar with architec...
0      1  Overview:How would you like to join an interna...
1      1  NET/JavaScript/DevOps/ ServiceNow /AI/ Cobol t...

In [102]:
review.head()

index                                            Summary          JobUrl
0      0  Company DescriptionSmartDev is a leading provi...  .NET Developer
1      1  Overview:How would you like to join an interna...  .NET Developer
2      2  Sioux Group was founded in 1996 in the Netherl...  .NET Developer
3      3  Up to $2,200Junior, Middle, SeniorDa NangFull-...  .NET Developer
4      4  Web Developer (.NET, ASP.NET, C#)NPV CorpỨng T...  .NET Developer

In [103]:
# merger data by index
review = review.merge(df, left_on = 'index', right_on = 'index')

In [104]:
review.shape

(84890, 4)

In [105]:
review = review.loc[review.duplicated() == False, :]

In [106]:
#find sentences with words in tool_keyword list
def filterString(string):
  item = string.split(' ')
  stemmed_tokens = [ps.stem(tok).lower() for tok in item]
  for st in stemmed_tokens:
    if tool_keywords1_set.__contains__(st):
      return string
  return None

In [107]:
review['review_filter'] = review['review'].apply(lambda string: filterString(string))

In [108]:
review['review_filter'].isna().sum()

64419

In [109]:
review.dropna(inplace=True)

In [110]:
review.isna().sum()

index            0
Summary          0
JobUrl           0
review           0
review_filter    0
dtype: int64

In [111]:
# Remove stopwords
review['Summary_without_stopwords'] = review['review'].apply(lambda x: ' '.join([w for w in x.split() if w.lower() not in stopwords]))

# Lemmatization
review['review_lemmatized'] = review['Summary_without_stopwords'].apply(lambda x: ' '.join([wn.lemmatize(w) for w in x.split() if w not in stopwords]))

# Take a look at the data
review.head()

index                                            Summary          JobUrl  \
8      0  Company DescriptionSmartDev is a leading provi...  .NET Developer   
9      0  Company DescriptionSmartDev is a leading provi...  .NET Developer   
10     0  Company DescriptionSmartDev is a leading provi...  .NET Developer   
11     0  Company DescriptionSmartDev is a leading provi...  .NET Developer   
12     0  Company DescriptionSmartDev is a leading provi...  .NET Developer   

                                               review  \
8   Net programming languagesTest and deploy appli...   
9                   Net DeveloperBe familiar with ASP   
10  NET framework, SQL Server and design/ architec...   
11                   Net languages (C#, Visual Basic    
12  Net), and HTML5/ CSS3Be familiar with architec...   

                                        review_filter  \
8   Net programming languagesTest and deploy appli...   
9                   Net DeveloperBe familiar with ASP   
10  NET framework, SQL Server and design/ architec...   
11                   Net languages (C#, Visual Basic    
12  Net), and HTML5/ CSS3Be familiar with architec...   

                            Summary_without_stopwords  \
8   Net programming languagesTest deploy applicati...   
9                        Net DeveloperBe familiar ASP   
10  NET framework, SQL Server design/ architectura...   
11                    Net languages (C#, Visual Basic   
12  Net), HTML5/ CSS3Be familiar architecture styl...   

                                    review_lemmatized  
8   Net programming languagesTest deploy applicati...  
9                        Net DeveloperBe familiar ASP  
10  NET framework, SQL Server design/ architectura...  
11                     Net language (C#, Visual Basic  
12  Net), HTML5/ CSS3Be familiar architecture styl...

In [112]:
review.isna().sum()

index                        0
Summary                      0
JobUrl                       0
review                       0
review_filter                0
Summary_without_stopwords    0
review_lemmatized            0
dtype: int64

In [113]:
review = review.loc[review.duplicated() == False, :]

In [114]:
review = review.reset_index()

In [115]:
review.shape

(16723, 8)

In [116]:
# Initiate UMAP to dimension reduction.
umap_model = UMAP(n_neighbors=15, 
                  n_components=5, 
                  min_dist=0.0, 
                  metric='cosine', 
                  random_state=100)

# Initiate BERTopic
topic_model = BERTopic(umap_model=umap_model, language="english", calculate_probabilities=True)

# Run BERTopic model
topics, probabilities = topic_model.fit_transform(review['review_lemmatized'])

In [117]:
# Get the list of topics
topic_model.get_topic_info()

Topic  Count                                               Name
0       -1   2851                          -1_data_business_vin_team
1        0    464                         0_thiuvic_clientl_tphcm_nc
2        1    460                                    1_ch_du_phc_khi
3        2    457             2_remote_rails_nnmanyear_developerupto
4        3     99                        3_gcp_cloud_azure_29yearend
..     ...    ...                                                ...
534    533     10                              533_cloud_amazon_aws_
535    534     10        534_campaign_targeting_competition_behavior
536    535     10  535_yearsqualificationsbachelor_degreepermtemp...
537    536     10  536_crosscultural_dedication_teamwork_communic...
538    537     10  537_developerproficiency_mysqlgood_systemexper...

[539 rows x 3 columns]

In [118]:
# Get top 10 terms for a topic
topic_model.get_topic(0)

[('thiuvic', 0.0499504216066022),
 ('clientl', 0.0499504216066022),
 ('tphcm', 0.04927133251580962),
 ('nc', 0.046369118766309364),
 ('ngoi', 0.04434459869531377),
 ('lnh', 0.04264304654414975),
 ('100', 0.04089765112276466),
 ('hot', 0.03862756485869755),
 ('vc', 0.03774730011375876),
 ('mm', 0.03535482091911907)]

In [119]:
# Visualize top topic keywords
topic_model.visualize_barchart(top_n_topics=20)

In [120]:
# Visualize term rank decrease
topic_model.visualize_term_rank()

In [121]:
# Visualize intertopic distance
topic_model.visualize_topics()

In [122]:
# Visualize connections between topics using hierachical clustering
topic_model.visualize_hierarchy(top_n_topics=15)

In [123]:
# Visualize similarity using heatmap
topic_model.visualize_heatmap()

In [124]:
# Check the content for the first review
review['review'][0]

'Net programming languagesTest and deploy application and systemsRevise, update, refactor and debugs codeDevelop documentation throughout the software development life cycleParticipate in code reviewsTrain fellow colleaguesQualificationsProven 3+ years of work experience as a '

In [125]:
# Get probabilities for all topics
topic_model.probabilities_[0][:30]

array([1.92720603e-05, 1.70043805e-05, 2.11923801e-05, 5.87710827e-05,
       2.45881702e-05, 4.45385932e-05, 2.91739457e-05, 1.81699283e-05,
       4.04307967e-05, 5.48326906e-05, 2.07998453e-05, 4.69464065e-05,
       3.76525269e-05, 4.20364065e-05, 2.28727247e-05, 5.94327305e-05,
       4.56252028e-05, 2.22216249e-05, 3.99072314e-05, 4.82860990e-05,
       3.99474096e-05, 5.75171696e-05, 4.69709046e-05, 4.98696327e-05,
       2.55244812e-05, 3.62648761e-05, 2.36311489e-05, 2.71928154e-05,
       3.67600309e-05, 5.25327277e-05])

In [126]:
# Get the topic predictions
topic_prediction = topic_model.topics_[:]

# Save the predictions in the dataframe
review['topic_prediction'] = topic_prediction

# Take a look at the data
review.head()

level_0 index                                            Summary  \
0        8     0  Company DescriptionSmartDev is a leading provi...   
1        9     0  Company DescriptionSmartDev is a leading provi...   
2       10     0  Company DescriptionSmartDev is a leading provi...   
3       11     0  Company DescriptionSmartDev is a leading provi...   
4       12     0  Company DescriptionSmartDev is a leading provi...   

           JobUrl                                             review  \
0  .NET Developer  Net programming languagesTest and deploy appli...   
1  .NET Developer                  Net DeveloperBe familiar with ASP   
2  .NET Developer  NET framework, SQL Server and design/ architec...   
3  .NET Developer                   Net languages (C#, Visual Basic    
4  .NET Developer  Net), and HTML5/ CSS3Be familiar with architec...   

                                       review_filter  \
0  Net programming languagesTest and deploy appli...   
1                  Net DeveloperBe familiar with ASP   
2  NET framework, SQL Server and design/ architec...   
3                   Net languages (C#, Visual Basic    
4  Net), and HTML5/ CSS3Be familiar with architec...   

                           Summary_without_stopwords  \
0  Net programming languagesTest deploy applicati...   
1                       Net DeveloperBe familiar ASP   
2  NET framework, SQL Server design/ architectura...   
3                    Net languages (C#, Visual Basic   
4  Net), HTML5/ CSS3Be familiar architecture styl...   

                                   review_lemmatized  topic_prediction  
0  Net programming languagesTest deploy applicati...                57  
1                       Net DeveloperBe familiar ASP               333  
2  NET framework, SQL Server design/ architectura...                -1  
3                     Net language (C#, Visual Basic                57  
4  Net), HTML5/ CSS3Be familiar architecture styl...               214

In [127]:
# New data for the review
new_review = "Having experience with Programing Language such as R Python Report/dashboard visualization Tableau Power BI Qlik is a plus."

# Find topics
num_of_topics = 3
similar_topics, similarity = topic_model.find_topics(new_review, top_n=num_of_topics); 

# Print results
print(f'The top {num_of_topics} similar topics are {similar_topics}, and the similarities are {np.round(similarity,2)}')

The top 3 similar topics are [11, 242, 22], and the similarities are [0.46 0.39 0.37]


In [128]:
# Print the top keywords for the top similar topics
for i in range(num_of_topics):
  print(f'The top keywords for topic {similar_topics[i]} are:')
  print(topic_model.get_topic(similar_topics[i]))

The top keywords for topic 11 are:
[('dashboard', 0.10869025186676255), ('visualization', 0.04470510881629173), ('forms', 0.033473004761414016), ('chart', 0.03048773615849215), ('bi', 0.030198355866221466), ('responsibilitiesresearch', 0.026895970556024187), ('power', 0.02632136737539697), ('report', 0.024991460487083048), ('reporting', 0.02396803091816152), ('workflow', 0.023499097892171632)]
The top keywords for topic 242 are:
[('programing', 0.08928179394921981), ('mysql', 0.0884747428005308), ('database', 0.08754011006178387), ('mssql', 0.08042963020619838), ('indepth', 0.06554107592576228), ('graph', 0.06522764585790243), ('kind', 0.0644232728126091), ('jdbc', 0.05628461795203819), ('sql', 0.049740848008776956), ('ms', 0.04678958461679432)]
The top keywords for topic 22 are:
[('data', 0.03287060134948888), ('analytics', 0.02201047977190685), ('insight', 0.021205452922376064), ('statistical', 0.01947136630052943), ('dashboard', 0.01585709865827786), ('bi', 0.013838464801756177), ('

In [129]:
# merge list job by topics
list_job = []
for i in range(num_of_topics):
  name =review.loc[review['topic_prediction'] == similar_topics[i],  'JobUrl']
  job = name.tolist()
  list_job += job
print(list_job)

['.NET Developer', '.NET Developer', '.NET Developer', '.NET Developer', '.NET Developer', 'Android App Developer', 'Android Developer', 'Back End Developer', 'Back End Developer', 'Back End Web Developer', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Analyst', 'Business Ana

In [130]:
# check the most appearing job
def most_frequent(List):
    return max(set(List), key = List.count)


In [131]:
most_frequent(list_job)

'Business Analyst'